# SNAP Grocery Stores

https://services1.arcgis.com/RLQu0rK7h4kbsBq5/arcgis/rest/services/Store_Locations/FeatureServer/0/query?where=1%3D1&outFields=*&outSR=4326&f=json

In [4]:
#dependencies
import pandas as pd
import json
import requests

In [5]:
#load the data
snap_data = json.loads(requests.get("https://services1.arcgis.com/RLQu0rK7h4kbsBq5/arcgis/rest/services/Store_Locations/FeatureServer/0/query?where=1%3D1&outFields=*&outSR=4326&f=json").text)
lr_data = json.loads(requests.get("https://opendata.arcgis.com/datasets/00a92b98e7fc4ef5999d68f9cb86c36f_1.geojson").text)
bs_data = json.loads(requests.get("https://opendata.arcgis.com/datasets/ba0a1ffe10d444cd9a3e7c2060f6969f_0.geojson").text)

# SNAP Stores

In [6]:
list(snap_data.keys())

['objectIdFieldName',
 'uniqueIdField',
 'globalIdFieldName',
 'geometryType',
 'spatialReference',
 'fields',
 'features']

In [7]:
df1 = pd.DataFrame(snap_data["features"])

In [8]:
df1.head()

attributes  \
0  {'Store_Name': 'DOLLARTREE 8500', 'Address': '...   
1  {'Store_Name': 'Meijer Gas Station 68', 'Addre...   
2  {'Store_Name': 'Meijer Gas Station 161', 'Addr...   
3  {'Store_Name': 'Mejier Gas Station 308', 'Addr...   
4  {'Store_Name': 'Meijer Gas Station 214', 'Addr...   

                                            geometry  
0  {'x': -82.05504600000002, 'y': 32.396796999999...  
1                  {'x': -83.405739, 'y': 42.332569}  
2          {'x': -84.418816, 'y': 38.02008399999999}  
3          {'x': -81.988991, 'y': 41.46113999999999}  
4          {'x': -88.201988, 'y': 41.63289300000001}

In [9]:
snap_df = df1["attributes"].apply(pd.Series)

In [10]:
snap_df.head()

Store_Name              Address Address_Line__2        City  \
0         DOLLARTREE 8500      978 SE Broad St            None      Metter   
1   Meijer Gas Station 68      37201 Warren Rd            None    Westland   
2  Meijer Gas Station 161  2145 Sir Barton Way            None   Lexington   
3  Mejier Gas Station 308        1820 Nagel Rd            None        Avon   
4  Meijer Gas Station 214     13705 S Route 59            None  Plainfield   

  State   Zip5  Zip4   County  Longitude   Latitude  ObjectId  
0    GA  30439  3933  CANDLER -82.055046  32.396797         1  
1    MI  48185  7219    WAYNE -83.405739  42.332569         2  
2    KY  40509  2203  FAYETTE -84.418816  38.020084         3  
3    OH  44011  1442   LORAIN -81.988991  41.461140         4  
4    IL  60544  6106     WILL -88.201988  41.632893         5

In [11]:
#keep only stores in AZ
snap_df = snap_df[snap_df["State"] == 'AZ']

In [12]:
snap_df.head()

Store_Name             Address Address_Line__2      City State  \
42     Kwik Corner 5059    5059 W Olive Ave            None  Glendale    AZ   
120   Grand Ave Produce   8990 W Windsor Dr            None    Peoria    AZ   
524  Big Az Market  2 2  51348 W Highway 60            None    Aguila    AZ   
549     Pride Food Mart  1734 E Apache Blvd            None     Tempe    AZ   
627     Caribbean Oasis      2958 N 16th St            None   Phoenix    AZ   

      Zip5  Zip4    County  Longitude   Latitude  ObjectId  
42   85302  3524  MARICOPA -112.16846  33.566959        43  
120  85381  6152  MARICOPA -112.25265  33.600914       121  
524  85320  0199  MARICOPA -113.17298  33.943394       525  
549  85281  5958  MARICOPA -111.90952  33.414875       550  
627  85016  7606  MARICOPA -112.04771  33.481934       628

In [13]:
request = json.loads(requests.get('https://geo.fcc.gov/api/census/block/find?latitude=38.26&longitude=-77.51&showall=false&format=json').text)
request['Block']['FIPS']    
    

'511770203042000'

In [31]:
result = []
for index, row in snap_df.iterrows():
    try:
        lat = row['Latitude']
        long = row['Longitude']
        url = f'https://geo.fcc.gov/api/census/block/find?latitude={lat}&longitude={long}&showall=false&format=json'
        request = json.loads(requests.get(url).text)
        print(request)
        result.append(request['Block']['FIPS'])
    except:
        result.append('NaN')
        
snap_df['FIPS'] = result
        

{'Block': {'FIPS': '040130923092004', 'bbox': [-112.168994, 33.563725, -112.166192, 33.567513]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040130715171009', 'bbox': [-112.259687, 33.595205, -112.247475, 33.602839]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040130405151290', 'bbox': [-113.176497, 33.942658, -113.167623, 33.944104]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040133191032005', 'bbox': [-111.91232, 33.414769, -111.909075, 33.416157]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coord

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131116022000', 'bbox': [-112.041139, 33.472051, -112.038935, 33.472985]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131070001000', 'bbox': [-112.137477, 33.536248, -112.134311, 33.538513]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131090034003', 'bbox': [-112.112581, 33.495016, -112.10

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040210002051000', 'bbox': [-111.563282, 33.237316, -111.552208, 33.249023]}, 'County': {'FIPS': '04021', 'name': 'Pinal'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131033042000', 'bbox': [-112.015638, 33.633538, -112.013445, 33.63708]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, th

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131061003007', 'bbox': [-112.0996, 33.538587, -112.095784, 33.542265]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040190040641046', 'bbox': [-110.728219, 32.12691, -110.721588, 32.129651]}, 'County': {'FIPS': '04019', 'name': 'Pima'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040019442021008', 'bbox': [-109.604495, 36.283516, -109.599532, 3

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040130932002006', 'bbox': [-112.237735, 33.559263, -112.228542, 33.566707]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040139804001018', 'bbox': [-111.968893, 33.302484, -111.967169, 33.305287]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040190029011009', 'bbox': [-110.899078, 32.25064, -110.892

...

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040199410002000', 'bbox': [-111.089728, 32.126233, -111.079534, 32.133441]}, 'County': {'FIPS': '04019', 'name': 'Pima'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040019702001851', 'bbox': [-109.848702, 34.283922, -109.82873, 34.301693]}, 'County': {'FIPS': '04001', 'name': 'Apache'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134212011015', 'bbox': [-111.874275, 33.429403, -111.856186, 3

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131052002003', 'bbox': [-112.065281, 33.558203, -112.063979, 33.560515]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040134211022015', 'bbox': [-111.84183, 33.422365, -111.839944, 33.423384]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131166063000', 'bbox': [-112.142399, 33.384791, -112.133

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131159001004', 'bbox': [-112.057514, 33.405065, -112.055635, 33.406746]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040136187002005', 'bbox': [-112.099753, 33.651072, -112.097609, 33.654733]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131125102026', 'bbox': [-112.232572, 33.440351, -112.229673, 33.443081]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boun

{'Block': {'FIPS': '040131047023015', 'bbox': [-112.060433, 33.571339, -112.056699, 33.572862]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040250008012004', 'bbox': [-112.46061, 34.539849, -112.459269, 34.541834]}, 'County': {'FIPS': '04025', 'name': 'Yavapai'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131136021009', 'bbox': [-112.012908, 33.457645, -112.010716, 33.458587]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040130609023003', 'bbox': [-112.32475

{'Block': {'FIPS': '040131071021009', 'bbox': [-112.151549, 33.509447, -112.147749, 33.51283]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131045023006', 'bbox': [-112.099586, 33.576895, -112.098227, 33.578479]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131091021005', 'bbox': [-112.134237, 33.495061, -112.130982, 33.498579]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040132179001001', 'bbox': [-111.911349, 33.479082, -111.909922, 33.479474]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '0401310590010

In [32]:
snap_df.head()

Store_Name             Address Address_Line__2      City State  \
42     Kwik Corner 5059    5059 W Olive Ave            None  Glendale    AZ   
120   Grand Ave Produce   8990 W Windsor Dr            None    Peoria    AZ   
524  Big Az Market  2 2  51348 W Highway 60            None    Aguila    AZ   
549     Pride Food Mart  1734 E Apache Blvd            None     Tempe    AZ   
627     Caribbean Oasis      2958 N 16th St            None   Phoenix    AZ   

      Zip5  Zip4    County  Longitude   Latitude  ObjectId             FIPS  
42   85302  3524  MARICOPA -112.16846  33.566959        43  040130923092004  
120  85381  6152  MARICOPA -112.25265  33.600914       121  040130715171009  
524  85320  0199  MARICOPA -113.17298  33.943394       525  040130405151290  
549  85281  5958  MARICOPA -111.90952  33.414875       550  040133191032005  
627  85016  7606  MARICOPA -112.04771  33.481934       628  040131106004015

In [35]:
snap_df['Census Tract'] = snap_df['FIPS'].str[:11]

In [36]:
snap_df.head()

Store_Name             Address Address_Line__2      City State  \
42     Kwik Corner 5059    5059 W Olive Ave            None  Glendale    AZ   
120   Grand Ave Produce   8990 W Windsor Dr            None    Peoria    AZ   
524  Big Az Market  2 2  51348 W Highway 60            None    Aguila    AZ   
549     Pride Food Mart  1734 E Apache Blvd            None     Tempe    AZ   
627     Caribbean Oasis      2958 N 16th St            None   Phoenix    AZ   

      Zip5  Zip4    County  Longitude   Latitude  ObjectId             FIPS  \
42   85302  3524  MARICOPA -112.16846  33.566959        43  040130923092004   
120  85381  6152  MARICOPA -112.25265  33.600914       121  040130715171009   
524  85320  0199  MARICOPA -113.17298  33.943394       525  040130405151290   
549  85281  5958  MARICOPA -111.90952  33.414875       550  040133191032005   
627  85016  7606  MARICOPA -112.04771  33.481934       628  040131106004015   

    Census Tract  
42   04013092309  
120  04013071517  
524  04013040515  
549  04013319103  
627  04013110600

In [37]:
snap_df.to_csv('snap.csv')

# Light Rail Data

In [21]:
lr_data

{'type': 'FeatureCollection',
 'name': 'VALLEYMETRO_LightRailStations',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'OBJECTID': 1,
    'StationId': 1,
    'StationName': '19th Avenue / Dunlap Avenue',
    'Jurisdiction': 'Phoenix',
    'StationStatus': 'In Operation',
    'POINT_X': -112.0993888,
    'POINT_Y': 33.56708951,
    'Image': 'https://farm8.staticflickr.com/7090/26530397293_0faa60e8de_b.jpg',
    'Image2': 'https://farm8.staticflickr.com/7641/27039654922_cec4d20e63_b.jpg',
    'TVM': None,
    'Bench': None,
    'TrashCan': None,
    'BikeRacks': None,
    'WaterFountain': None,
    'Restroom': None,
    'InfoDisplay': None,
    'Em_Call': None,
    'NextRide': 18608,
    'Address': '1935 W Dunlap Ave'},
   'geometry': {'type': 'Point',
    'coordinates': [-112.10075946599994, 33.56739749700006]}},
  {'type': 'Feature',
   'properties': {'OBJECTID': 2,
    'StationId': 35,
    'Stati

In [22]:
df2 = pd.DataFrame(lr_data['features'])

In [23]:
df2.head()

type                                         properties  \
0  Feature  {'OBJECTID': 1, 'StationId': 1, 'StationName':...   
1  Feature  {'OBJECTID': 2, 'StationId': 35, 'StationName'...   
2  Feature  {'OBJECTID': 3, 'StationId': 2, 'StationName':...   
3  Feature  {'OBJECTID': 4, 'StationId': 3, 'StationName':...   
4  Feature  {'OBJECTID': 5, 'StationId': 21, 'StationName'...   

                                            geometry  
0  {'type': 'Point', 'coordinates': [-112.1007594...  
1  {'type': 'Point', 'coordinates': [-111.8306459...  
2  {'type': 'Point', 'coordinates': [-112.0996289...  
3  {'type': 'Point', 'coordinates': [-112.0997008...  
4  {'type': 'Point', 'coordinates': [-111.9879831...

In [24]:
lr_df = df2["properties"].apply(pd.Series)

In [25]:
lr_df.head()

OBJECTID  StationId                    StationName Jurisdiction  \
0         1          1    19th Avenue / Dunlap Avenue      Phoenix   
1         2         35    Center Street / Main Street         Mesa   
2         3          2  19th Avenue / Northern Avenue      Phoenix   
3         4          3  19th Avenue / Glendale Avenue      Phoenix   
4         5         21       44th Street / Washington      Phoenix   

  StationStatus     POINT_X    POINT_Y  \
0  In Operation -112.099389  33.567090   
1  In Operation -111.830660  33.415098   
2  In Operation -112.099360  33.553190   
3  In Operation -112.099329  33.538643   
4  In Operation -111.987983  33.448170   

                                               Image  \
0  https://farm8.staticflickr.com/7090/2653039729...   
1  https://farm6.staticflickr.com/5812/2398469262...   
2  https://farm8.staticflickr.com/7505/2710105440...   
3  https://farm8.staticflickr.com/7167/2653039369...   
4  https://farm6.staticflickr.com/5771/2343906011...   

                                              Image2  TVM  Bench  TrashCan  \
0  https://farm8.staticflickr.com/7641/2703965492...  NaN    NaN       NaN   
1                                               None  NaN    NaN       NaN   
2                                               None  NaN    NaN       NaN   
3  https://farm8.staticflickr.com/7377/2686011248...  NaN    NaN       NaN   
4  https://farm2.staticflickr.com/1502/2344359052...  NaN    NaN       NaN   

  BikeRacks WaterFountain Restroom InfoDisplay Em_Call  NextRide  \
0      None          None     None        None    None     18608   
1      None          None     None        None    None     18602   
2      None          None     None        None    None     18607   
3      None          None     None        None    None     18606   
4      None          None     None        None    None     10018   

                       Address  
0            1935 W Dunlap Ave  
1          26 East Main Street  
2              7832 N 19th Ave  
3              6813 N 19th Ave  
4  4203 East Washington Street

In [38]:
result2 = []
for index, row in lr_df.iterrows():
    try:
        lat = row['POINT_Y']
        long = row['POINT_X']
        url = f'https://geo.fcc.gov/api/census/block/find?latitude={lat}&longitude={long}&showall=false&format=json'
        request = json.loads(requests.get(url).text)
        print(request)
        result2.append(request['Block']['FIPS'])
    except:
        result2.append('NaN')
        
lr_df['FIPS'] = result2

{'Block': {'FIPS': '040131054002012', 'bbox': [-112.099643, 33.565055, -112.096925, 33.567609]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040134214001019', 'bbox': [-111.831473, 33.415089, -111.828872, 33.416202]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040131054003002', 'bbox': [-112.099675, 33.553051, -112.09126, 33.560431]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the bound

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040133190004007', 'bbox': [-111.928964, 33.420264, -111.926294, 33.420892]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040133187002004', 'bbox': [-111.942798, 33.427383, -111.940007, 33.429572]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131105013017', 'bbox': [-112.075023, 33.481226, -112.07

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131141001040', 'bbox': [-112.077668, 33.447148, -112.075101, 33.448248]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040134215011002', 'bbox': [-111.822958, 33.412881, -111.821809, 33.415079]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131171001020', 'bbox': [-112.078171, 33.494828, -112.07378, 33.496651]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131171001008', 'bbox': [-112.074912, 33.500217, -112.073767, 33.502046]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks,

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131140001027', 'bbox': [-112.05642, 33.447176, -112.054214, 33.448286]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131130001027', 'bbox': [-112.074603, 33.458627, -112.073772, 33.459983]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks,

In [39]:
lr_df.head()

OBJECTID  StationId                    StationName Jurisdiction  \
0         1          1    19th Avenue / Dunlap Avenue      Phoenix   
1         2         35    Center Street / Main Street         Mesa   
2         3          2  19th Avenue / Northern Avenue      Phoenix   
3         4          3  19th Avenue / Glendale Avenue      Phoenix   
4         5         21       44th Street / Washington      Phoenix   

  StationStatus     POINT_X    POINT_Y  \
0  In Operation -112.099389  33.567090   
1  In Operation -111.830660  33.415098   
2  In Operation -112.099360  33.553190   
3  In Operation -112.099329  33.538643   
4  In Operation -111.987983  33.448170   

                                               Image  \
0  https://farm8.staticflickr.com/7090/2653039729...   
1  https://farm6.staticflickr.com/5812/2398469262...   
2  https://farm8.staticflickr.com/7505/2710105440...   
3  https://farm8.staticflickr.com/7167/2653039369...   
4  https://farm6.staticflickr.com/5771/2343906011...   

                                              Image2  TVM  Bench  TrashCan  \
0  https://farm8.staticflickr.com/7641/2703965492...  NaN    NaN       NaN   
1                                               None  NaN    NaN       NaN   
2                                               None  NaN    NaN       NaN   
3  https://farm8.staticflickr.com/7377/2686011248...  NaN    NaN       NaN   
4  https://farm2.staticflickr.com/1502/2344359052...  NaN    NaN       NaN   

  BikeRacks WaterFountain Restroom InfoDisplay Em_Call  NextRide  \
0      None          None     None        None    None     18608   
1      None          None     None        None    None     18602   
2      None          None     None        None    None     18607   
3      None          None     None        None    None     18606   
4      None          None     None        None    None     10018   

                       Address             FIPS  
0            1935 W Dunlap Ave  040131054002012  
1          26 East Main Street  040134214001019  
2              7832 N 19th Ave  040131054003002  
3              6813 N 19th Ave  040131061003007  
4  4203 East Washington Street  040131138011012

In [40]:
lr_df['Census Tract'] = lr_df['FIPS'].str[:11]

In [41]:
lr_df.head()

OBJECTID  StationId                    StationName Jurisdiction  \
0         1          1    19th Avenue / Dunlap Avenue      Phoenix   
1         2         35    Center Street / Main Street         Mesa   
2         3          2  19th Avenue / Northern Avenue      Phoenix   
3         4          3  19th Avenue / Glendale Avenue      Phoenix   
4         5         21       44th Street / Washington      Phoenix   

  StationStatus     POINT_X    POINT_Y  \
0  In Operation -112.099389  33.567090   
1  In Operation -111.830660  33.415098   
2  In Operation -112.099360  33.553190   
3  In Operation -112.099329  33.538643   
4  In Operation -111.987983  33.448170   

                                               Image  \
0  https://farm8.staticflickr.com/7090/2653039729...   
1  https://farm6.staticflickr.com/5812/2398469262...   
2  https://farm8.staticflickr.com/7505/2710105440...   
3  https://farm8.staticflickr.com/7167/2653039369...   
4  https://farm6.staticflickr.com/5771/2343906011...   

                                              Image2  TVM  ...  TrashCan  \
0  https://farm8.staticflickr.com/7641/2703965492...  NaN  ...       NaN   
1                                               None  NaN  ...       NaN   
2                                               None  NaN  ...       NaN   
3  https://farm8.staticflickr.com/7377/2686011248...  NaN  ...       NaN   
4  https://farm2.staticflickr.com/1502/2344359052...  NaN  ...       NaN   

   BikeRacks WaterFountain Restroom InfoDisplay Em_Call NextRide  \
0       None          None     None        None    None    18608   
1       None          None     None        None    None    18602   
2       None          None     None        None    None    18607   
3       None          None     None        None    None    18606   
4       None          None     None        None    None    10018   

                       Address             FIPS Census Tract  
0            1935 W Dunlap Ave  040131054002012  04013105400  
1          26 East Main Street  040134214001019  04013421400  
2              7832 N 19th Ave  040131054003002  04013105400  
3              6813 N 19th Ave  040131061003007  04013106100  
4  4203 East Washington Street  040131138011012  04013113801  

[5 rows x 21 columns]

In [42]:
lr_df.to_csv('lr.csv')

# Bus Stop Data

In [26]:
bs_data

{'type': 'FeatureCollection',
 'name': 'Valley_Metro_Bus_Stops_View',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'OBJECTID': 1,
    'StopID': 5182,
    'NextRide': 16020,
    'Location': 'MESA DR & MAIN ST',
    'Juris': 'Mesa',
    'Shelter': 1,
    'Bench': 1,
    'TrashCan': 0,
    'BusBay': 'No',
    'BikeRack': 0,
    'WaterFountain': 'No',
    'PublicArt': 'No',
    'ADA': 'No',
    'Bathroom': 'No',
    'Lighting': 'No',
    'Em_Call': 'No',
    'Info_Display': 'No',
    'Type_': 'Standard',
    'DateUpdated': 1541147907453,
    'Sidewalk': None,
    'Photo': 'https://farm9.staticflickr.com/8719/16921707206_868c4c2c60_o.jpg',
    'ATIS_ID': 5196,
    'Direction': 'Southbound',
    'Long': -111.823075990545,
    'Lat': 33.4147193304186,
    'Routes': '120'},
   'geometry': {'type': 'Point',
    'coordinates': [-111.823075990545, 33.4147193304186]}},
  {'type': 'Feature',
   'properties':

In [27]:
df3 = pd.DataFrame(bs_data["features"])

In [28]:
bs_df = df3["properties"].apply(pd.Series)

In [29]:
bs_df.head()

OBJECTID  StopID  NextRide                 Location Juris  Shelter  Bench  \
0       1.0  5182.0   16020.0        MESA DR & MAIN ST  Mesa      1.0    1.0   
1       2.0  2982.0   16001.0        MESA DR & MAIN ST  Mesa      1.0    4.0   
2       3.0  4681.0   16016.0         MESA DR & 6TH ST  Mesa      1.0    1.0   
3       4.0  4682.0   16017.0  MESA DR & UNIVERSITY DR  Mesa      1.0    1.0   
4       5.0  4679.0   16019.0         MESA DR & 1ST ST  Mesa      0.0    1.0   

   TrashCan BusBay  BikeRack  ... Info_Display     Type_   DateUpdated  \
0       0.0     No       0.0  ...           No  Standard  1.541148e+12   
1       1.0    Yes       2.0  ...          Yes      LINK  1.541148e+12   
2       1.0     No       2.0  ...           No  Standard  1.541148e+12   
3       1.0     No       0.0  ...           No  Standard  1.541148e+12   
4       1.0     No       0.0  ...           No  Standard  1.541148e+12   

  Sidewalk                                              Photo ATIS_ID  \
0     None  https://farm9.staticflickr.com/8719/1692170720...  5196.0   
1      Yes  https://farm1.staticflickr.com/757/21334866928...  2996.0   
2      Yes  https://farm8.staticflickr.com/7288/1632759920...  4695.0   
3      Yes  https://farm9.staticflickr.com/8622/1630995151...  4696.0   
4      Yes  https://farm8.staticflickr.com/7292/1587753502...  4693.0   

    Direction        Long        Lat Routes  
0  Southbound -111.823076  33.414719    120  
1  Northbound -111.822766  33.415684    120  
2  Southbound -111.822934  33.425734    120  
3  Southbound -111.823048  33.422048    120  
4  Southbound -111.823069  33.416883    120  

[5 rows x 26 columns]

In [43]:
result3 = []
for index, row in bs_df.iterrows():
    try:
        lat = row['Lat']
        long = row['Long']
        url = f'https://geo.fcc.gov/api/census/block/find?latitude={lat}&longitude={long}&showall=false&format=json'
        request = json.loads(requests.get(url).text)
        print(request)
        result3.append(request['Block']['FIPS'])
    except:
        result3.append('NaN')
        
bs_df['FIPS'] = result3

{'Block': {'FIPS': '040134214002000', 'bbox': [-111.824583, 33.41422, -111.822943, 33.41508]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134215022015', 'bbox': [-111.822943, 33.415076, -111.820572, 33.417253]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134210021012', 'bbox': [-111.823725, 33.425067, -111.822802, 33.425993]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134214001000', 'bbox': [-111.823673, 33.419418, -111.822872, 33.422376]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '04013421400101

{'Block': {'FIPS': '040134205041002', 'bbox': [-111.808734, 33.445596, -111.80498, 33.44786]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134205042000', 'bbox': [-111.813793, 33.443139, -111.805037, 33.445614]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134205042032', 'bbox': [-111.810889, 33.438122, -111.805155, 33.441322]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134205042040', 'bbox': [-111.807074, 33.43609, -111.80528, 33.437033]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134209011007'

{'Block': {'FIPS': '040134203023021', 'bbox': [-111.789846, 33.457969, -111.780431, 33.466537]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040138124001010', 'bbox': [-111.806931, 33.277138, -111.789674, 33.282496]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134224041002', 'bbox': [-111.78993, 33.336163, -111.77965, 33.350028]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040138144002012', 'bbox': [-111.79054, 33.330483, -111.783877, 33.335502]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134224023021

{'Block': {'FIPS': '040134208002001', 'bbox': [-111.80528, 33.430529, -111.800777, 33.434354]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134225082005', 'bbox': [-111.790021, 33.364449, -111.782055, 33.37174]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134208004016', 'bbox': [-111.791778, 33.43065, -111.787944, 33.434164]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040134224041000', 'bbox': [-111.789452

{'Block': {'FIPS': '040134206042025', 'bbox': [-111.80528, 33.437033, -111.803183, 33.43985]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040134206042024', 'bbox': [-111.792208, 33.43911, -111.787829, 33.440364]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134225081006', 'bbox': [-111.790062, 33.371671, -111.78522, 33.378824]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134202021000', 'bbox': [-111.686362,

...

{'Block': {'FIPS': '040132168371008', 'bbox': [-111.838577, 33.589208, -111.833944, 33.593259]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040132168372014', 'bbox': [-111.842679, 33.591448, -111.838577, 33.595171]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040132168372010', 'bbox': [-111.846259, 33.588715, -111.84

{'Block': {'FIPS': '040130715142022', 'bbox': [-112.246367, 33.635409, -112.241983, 33.638164]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040130715142019', 'bbox': [-112.252353, 33.624262, -112.239814, 33.638156]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040136176003014', 'bbox': [-112.246325, 33.638142, -112.241745, 33.640265]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040136176001011', 'bbox': [-112.250668, 33.638131, -112.246323, 33.643184]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040136176002

{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040133191032008', 'bbox': [-111.917723, 33.414771, -111.91473, 33.416938]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040133191033000', 'bbox': [-111.91768, 33.41932, -111.909058, 33.422027]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040133191031013', 'bbox': [-111.9263, 33.417501, -111.91768, 

{'Block': {'FIPS': '040134216022000', 'bbox': [-111.794455, 33.412413, -111.788235, 33.415391]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134216022000', 'bbox': [-111.794455, 33.412413, -111.788235, 33.415391]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134216022000', 'bbox': [-111.794455, 33.412413, -111.788235, 33.415391]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040134213024006', 'bbox': [-111.842096, 33.412413, -111.839904, 33.413309]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040136160001

{'Block': {'FIPS': '040130610152003', 'bbox': [-112.340948, 33.464182, -112.334941, 33.471532]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040130610203012', 'bbox': [-112.369155, 33.481171, -112.36226, 33.485864]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'Block': {'FIPS': '040130610203003', 'bbox': [-112.362575, 33.485388, -112.358107, 33.48606]}, 'County': {'FIPS': '04013', 'name': 'Maricopa'}, 'State': {'FIPS': '04', 'code': 'AZ', 'name': 'Arizona'}, 'status': 'OK', 'executionTime': '0'}
{'messages': ["FCC0001: The coordinate lies on the boundary of mulitple blocks, the block contains the clicked location is selected. For a complete list use showall=true to display 'intersection' element in the Block"], 'Block': {'FIPS': '040131167252004', 'bbox': [-112.05994

In [44]:
bs_df['Census Tract'] = bs_df['FIPS'].str[:11]

In [45]:
bs_df.head()

OBJECTID  StopID  NextRide                 Location Juris  Shelter  Bench  \
0       1.0  5182.0   16020.0        MESA DR & MAIN ST  Mesa      1.0    1.0   
1       2.0  2982.0   16001.0        MESA DR & MAIN ST  Mesa      1.0    4.0   
2       3.0  4681.0   16016.0         MESA DR & 6TH ST  Mesa      1.0    1.0   
3       4.0  4682.0   16017.0  MESA DR & UNIVERSITY DR  Mesa      1.0    1.0   
4       5.0  4679.0   16019.0         MESA DR & 1ST ST  Mesa      0.0    1.0   

   TrashCan BusBay  BikeRack  ...   DateUpdated Sidewalk  \
0       0.0     No       0.0  ...  1.541148e+12     None   
1       1.0    Yes       2.0  ...  1.541148e+12      Yes   
2       1.0     No       2.0  ...  1.541148e+12      Yes   
3       1.0     No       0.0  ...  1.541148e+12      Yes   
4       1.0     No       0.0  ...  1.541148e+12      Yes   

                                               Photo ATIS_ID   Direction  \
0  https://farm9.staticflickr.com/8719/1692170720...  5196.0  Southbound   
1  https://farm1.staticflickr.com/757/21334866928...  2996.0  Northbound   
2  https://farm8.staticflickr.com/7288/1632759920...  4695.0  Southbound   
3  https://farm9.staticflickr.com/8622/1630995151...  4696.0  Southbound   
4  https://farm8.staticflickr.com/7292/1587753502...  4693.0  Southbound   

         Long        Lat Routes             FIPS Census Tract  
0 -111.823076  33.414719    120  040134214002000  04013421400  
1 -111.822766  33.415684    120  040134215022015  04013421502  
2 -111.822934  33.425734    120  040134210021012  04013421002  
3 -111.823048  33.422048    120  040134214001000  04013421400  
4 -111.823069  33.416883    120  040134214001015  04013421400  

[5 rows x 28 columns]

In [46]:
bs_df.to_csv('bs.csv')

# Distance

In [ ]:
#Okay here is the plan
#get a unique list of values for the Census Tract Scores! Con